In [ ]:
# 安裝 D-Wave 量子退火套件與 pyqubo
!pip install dwave-ocean-sdk
!pip install pyqubo

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 160.8/160.8 kB 6.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 37.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.3/78.3 kB 6.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 64.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 14.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.0/9.0 MB 75.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 106.9/106.9 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.9/3.9 MB 30.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.1/232.1 kB 17.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.5/45.5 kB 2.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 258.3/258.3 kB 6.8 MB/s eta 0:00:00


In [ ]:
"""
引入 Pyqubo 中的 Binary 變數類別
更多資料：https://pyqubo.readthedocs.io/en/latest/reference/express.html?highlight=binary#pyqubo.Binary
"""
from pyqubo import Binary

# QUBO 簡介
QUBO 是一種二元優化問題的表達形式，目標是透過調整一組二元變數來最小化一個二次目標函數。QUBO 主要形式如下：
​$f(x)=\Sigma_i Q_{ii}x_i+\Sigma_{i\neq j}Q_{ij}x_i x_j$
其中：
$x_i$​ 為二元變數（0 或 1）。
$Q_{ii}$ 和 $Q_{ij}$​ 是 Q 矩陣中的係數。

QUBO 常應用於組合優化問題，如最大割 (Max-Cut)、旅行推銷員問題 (TSP)，以及子集和問題 (Subset Sum Problem)。

#Subset Sum Problem 簡述

Subset Sum Problem 是一個經典的 NP 完全問題。給定一組整數和一個目標值 target，目標是在這些整數中找出一個子集，使其和等於 target。
# 問題轉換

假設我們有一組整數 ${A_1,A_2,…,A_n}$ 和一個目標值 target，我們希望選擇這組整數的某個子集，使其和為 target。我們可以將此問題轉換為 QUBO 的形式，具體步驟如下：

## 定義二元變數：
將每個整數 $A_i$​ 對應到一個二元變數 $x_i$​，若 $x_i=1$，表示選擇 $A_i$​ 作為子集的一部分；若 $x_i=0$，表示不選擇該數。

構建 QUBO 目標函數：

目標是使選擇的整數和 target 盡可能接近，即希望滿足：


$\Sigma_i^n A_i x_i = target$

將其轉換為一個 QUBO 目標函數，可以表示為對此和與目標值 target 之間的差平方最小化：

$(\Sigma_i^n A_i x_i - target)^2 $

展開並簡化：

將上述目標函數展開後，我們得到一個二次項與一次項組成的函數：

其中常數項對優化過程無影響，可以忽略。因此我們最小化以下目標函數：

轉換成 QUBO 矩陣：
根據展開的式子，我們可以將 QUBO 問題表示為矩陣 Q 的形式，並將其輸入到量子計算機或經典優化算法中進行求解。

In [ ]:
# 定義子集合問題資料
A = [1, 2, 3, 4] # 定義集合元素
n = len(A)
target = 5 # 定義子集和的目標


In [ ]:
"""
宣告一個變數 H，H 表示 Hamiltonian 是描述系統能量的函數，我們將需要最小化的函數視為系統能量（Hamiltonian），定義目標函數。
首先，我們需要初始化 H 變數為 0 即可。
"""
H = 0

"""
因為我們有 n 個元素，所以定義 n 個二元變數，xi 變數用來決定集合中的第 i 個元素是否放入子集中（如果 xi 為 1 則放入，為 0 則不放入）。
e.g. x = [Binary(x0), Binary(x1), Binary(x2), Binary(x3)]。
Binary 是宣告二元變數變數，讓程式知道這是二元變數，Pyqubo 就會將 H 視為一個可以轉換成 QUBO 的目標函數。
Binary("x") 是指建構一個 Label 為 "x" 的 Binary 變數 Object
"""
x = [Binary('x'+str(i)) for i in range(n)]



In [ ]:
"""
定義目標函式，
首先，我們將計算 A[i]*x[i] 總和
e.g. H = A[0]*x[0]+A[1]*x[1]+A[2]*x[2]+A[3]*x[3]

接著我們將這個總和減去目標後平方。
e.g. H = ((A[0]*x[0]+A[1]*x[1]+A[2]*x[2]+A[3]*x[3])-5)^2

量子退火的目標是要找到若干組 x 變數的值（0 或 1）可以使得能量（H）最小。
"""
for i in range(len(A)): # 總和所有的 A[i] * x[i]
  H += A[i]*x[i]

H -= target # (總和 - 目標)
H = H*H # (總和 - 目標)^2


In [ ]:
"""
最後，我們要將目標函式編譯成 QUBO 形式。
H.compile() 將 H 編譯成 Pyqubo 的 Model 物件，這個 Model 物件是一個用來描述目標函式的抽象物件，它具備將目標函式轉換成 qubo、ising、bqm 等形式的 Method。
[Model 文件](https://pyqubo.readthedocs.io/en/latest/reference/model.html#pyqubo.to_qubo)

model.to_qubo() 會回傳一個 tuple 為 (QUBO矩陣, 能量偏移量 offset)，QUBO 矩陣是用一個字典（dictionary）描述，格式為 {('變數j', '變數i'): Qij 的值}，另外 Qij 的值同時就代表 QUBO 中 xi*xj 項的係數。
[to_qubo() 文件](https://pyqubo.readthedocs.io/en/latest/reference/model.html#pyqubo.to_qubo)
註：offset 是 pyqubo 轉換為 qubo 的過程中所產生的常數項，通常可以忽略。在後續的返回的結果中得到的 energy 加上 offset 就是我們原先定義 H 的值。
"""
model = H.compile()
Q, offset = model.to_qubo() # 將目標函數轉換成 QUBO 形式
print(Q) # 印出 QUBO 矩陣

{('x2', 'x0'): 6.0, ('x3', 'x2'): 24.0, ('x3', 'x3'): -24.0, ('x2', 'x1'): 12.0, ('x3', 'x1'): 16.0, ('x3', 'x0'): 8.0, ('x2', 'x2'): -21.0, ('x0', 'x0'): -9.0, ('x1', 'x0'): 4.0, ('x1', 'x1'): -16.0}


In [ ]:
from dwave.samplers import SimulatedAnnealingSampler
sampler = SimulatedAnnealingSampler() # 宣告 Sampler
sampleset = sampler.sample_qubo(Q, num_reads=1000) # 求解 Q，取樣 1000 次
best_sample = sampleset.first.sample # 將能量最低的解拿出來
print("best solution: ", best_sample)
print("Hamiltonian: ", sampleset.first.energy+offset)

best solution:  {'x0': np.int8(0), 'x1': np.int8(1), 'x2': np.int8(1), 'x3': np.int8(0)}
Hamiltonian:  0.0


In [ ]:
# 檢查解答是否符合要求
total = 0
for i in range(len(A)):
    if best_sample[f'x{i}'] == 1:
        total += A[i]

print(total == target)

True


# Vertex Cover Problem
圖的覆蓋是一個頂點的集合，使圖中的每一條邊都至少連結該集合中的一個頂點。尋找最小的頂點覆蓋的問題稱為頂點覆蓋問題（Vertex cover），它是一個NP完全問題。
假設有一無向圖 $G = (V, E)$，其中 $V$ 為頂點集合，$E$ 為邊集合。頂點覆蓋是指從 $V$ 中選出一個子集 $C \subseteq V$，使得圖中每條邊 $e = (u, v)$ 至少有一個端點屬於 $C$。也就是說，對於所有邊 $(u,v) \in E$，必有 $u \in C$ 或 $v \in C$（或兩者皆屬）。

下圖是兩個頂點覆蓋問題的範例，紅點表示對於該圖來說的某個頂點覆蓋集合。 QUBO 的目標是求使用最少個頂點形成一個頂點覆蓋集。

Vertex-cover.svg
# 期中專案
期中專案請大家利用量子退火求解頂點覆蓋問題。程式至少能夠解決 keller4.mis 資料集，keller4 的最小覆蓋集是使用 160 個頂點，程式應該要輸出使用的頂點個數為 160。

報告書應包含：
1. 問題說明
2. QUBO 公式
3. 實驗結果
4. 心得

\\

其餘不拘。

## 評分標準
- 正確寫出 QUBO，並且能解決 keller4.mis 資料集 (40%)
- 問題描述和如何寫成 QUBO (15%)
- 說明實驗結果，實驗結果要比較使用的頂點個數（越少越好）。(10%)
- 解決 ee-class 上的其他資料集，有些資料集比較困難的可能需要嘗試調整 QUBO 權重，呈現在實驗結果當中，並說明使用哪些技巧進行實驗以及對結果的影響（如果有的話）(20%)
- 結論與心得(15%)

## 其他資料集
包含 keller4.mis 在內，我們還提供了另外五個資料集，作為 20% 中的分數，分別為 keller5、keller6、p_hat300-1、p_hat700-1和p_hat1500-1，這些資料集會上傳到 ee-class 作業區的 dataset.zip 中。



請利用這些資料集進行實驗，提出一個方法改進 QUBO 求解 VCP 的結果，在報告中說明你提出的方法，以及對於頂點覆蓋集的大小和結果有什麼影響。

# 資料集
資料的形式為 Edge List，以 keller4.mis 為例，部分資料如下，第一行是 `p edge 點的數量 邊的數量`，接著每一行描述一個邊所連接的兩個頂點 `e 頂點 頂點`。

keller4.mis 資料集：
```
p edge 171 5100                                   
e 1 2
e 1 3
e 1 4
e 1 5
e 1 6
e 1 7
e 1 9
e 1 10
e 1 11
e 1 18
e 1 28
e 1 29
e 1 31
e 1 32
.
.
.
```

下列程式碼將呈現如何讀入資料集，並且建構該圖的 networkx Grahp 物件。
networkx 是一個 python 套件，主要用來分析圖、網路等。我們將使用這個套件來儲存圖。
Network x: https://networkx.org/

In [ ]:
import networkx as nx

In [ ]:
#讀取data
path = f'/content/drive/MyDrive/Colab Notebooks/VertexCover/data/keller4.mis' # 資料集路徑
instance = [] # 宣告一個空串列，將每條邊存入 instance 中
with open(path) as f: # 讀取資料集的檔案
    for line in f.readlines():
        first_node = line.split()[1] # 將每條邊連接的兩個頂點拿出來，命名為 first_node 與 second_node
        second_node = line.split()[2]
        if len(instance) != 0:
          first_node = int(first_node)
          second_node = int(second_node)
        edge = (first_node,second_node) # 將一條邊組成一個 tuple 並且存入 instance 中
        instance.append(edge)
instance.pop(0) # 將第一行移除，因為第一行只有描述這張圖的點數和邊數，並不是描述邊

G = nx.Graph() # 建立一個圖物件，命名為 G
G.add_edges_from(instance) # 讓 G 根據 instance 的資料建構圖